In [1]:
from langchain_community.agent_toolkits import create_sql_agent
from langchain_openai import ChatOpenAI
from langchain_groq import ChatGroq
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.pydantic_v1 import BaseModel, Field
import pandas as pd
from pydantic import BaseModel, Field

from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.vectorstores import Chroma
from langchain.embeddings import HuggingFaceEmbeddings
from langchain_core.runnables import RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser


gpt = ChatOpenAI(model="gpt-3.5-turbo", temperature=0)
#agent_gpt_executor = create_sql_agent(gpt, db=db, agent_type="tool-calling", verbose=True)

## make database
from langchain_community.utilities import SQLDatabase
from sqlalchemy import create_engine

from langchain.prompts import ChatPromptTemplate
from langchain.schema import SystemMessage
from langchain_core.prompts import MessagesPlaceholder
#agent_groq_executor = create_sql_agent(llm, db=db, agent_type="tool-calling", verbose=True)

from OpenAITools.FetchTools import fetch_clinical_trials, fetch_clinical_trials_jp
from OpenAITools.CrinicalTrialTools import QuestionModifierEnglish, TumorNameExtractor, SimpleClinicalTrialAgent,GraderAgent,LLMTranslator,generate_ex_question_English

from OpenAITools.JRCTTools import get_matched_df,GetJRCTCriteria
from sentence_transformers import SentenceTransformer
from sentence_transformers import util
groq = ChatGroq(model_name="llama3-70b-8192", temperature=0)
#agent_groq_executor = create_sql_agent(groq, db=db, agent_type="tool-calling", verbose=True)

import ast
import torch
age = "65"
sex ="男性"
tumor_type ="glioma"
#tumor_type = "gastric cancer"
GeneMutation ="HER2"
Meseable = "有り"
Biopsiable = "有り"
NCTID = 'NCT06441994'

#Define extractor
Translator = LLMTranslator(groq)
TumorName = Translator.translate(tumor_type)
selectionModel =  SentenceTransformer('pritamdeka/S-PubMedBert-MS-MARCO')
ex_question = generate_ex_question_English(age, sex, TumorName, GeneMutation, Meseable, Biopsiable)

/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/IPython/core/interactiveshell.py:3577: LangChainDeprecationWarning: As of langchain-core 0.3.0, LangChain uses pydantic v2 internally. The langchain_core.pydantic_v1 module was a compatibility shim for pydantic v1, and should no longer be used. Please update the code to import from Pydantic directly.

For example, replace imports like: `from langchain_core.pydantic_v1 import BaseModel`
with: `from pydantic import BaseModel`
or the v1 compatibility namespace if you are working in a code base that has not been fully upgraded to pydantic 2 yet. 	from pydantic.v1 import BaseModel

  exec(code_obj, self.user_global_ns, self.user_ns)
/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import 

In [2]:
basedf = pd.read_csv("../ClinicalTrialCSV/JRCT20241215CancerPost.csv", index_col=0)

In [3]:
df = get_matched_df(basedf=basedf, query=TumorName, model=selectionModel, threshold=0.925)
df['AgentJudgment'] = None
df['AgentGrade'] = None

/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_52046/2492212482.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['AgentJudgment'] = None
/var/folders/yw/qz00x75d7kb98f7vm8dkhkvw0000gn/T/ipykernel_52046/2492212482.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['AgentGrade'] = None


In [5]:
CriteriaCheckAgent = SimpleClinicalTrialAgent(groq)
grader_agent = GraderAgent(groq)

In [6]:
for i in range(len(df)):
    TargetCriteria = GetJRCTCriteria(df, i)
    AgentJudgment = CriteriaCheckAgent.evaluate_eligibility(TargetCriteria, ex_question)
    print(AgentJudgment)
    AgentGrade = grader_agent.evaluate_eligibility(AgentJudgment)
    print(AgentGrade)
    
    # df.locを使って値を代入（行・列名で指定）
    df.loc[df.index[i], 'AgentJudgment'] = AgentJudgment
    df.loc[df.index[i], 'AgentGrade'] = AgentGrade


The patient is eligible for this clinical trial based on the provided information, as there are no exclusion criteria that would prevent him from participating.
yes
The patient is eligible for this clinical trial based on the provided criteria, as the patient's age (65) falls within the specified range (18-75), and there is no mention of any exclusion criteria being met.
yes
The patient is not eligible for this clinical trial because the patient's age (65) exceeds the upper limit of 75 years old specified in inclusion criterion (7).
no
Based on the provided information, the patient is eligible for this clinical trial. The patient meets the inclusion criteria for Cohort 1, as they have a glioma (WHO Grade 2-4) diagnosed by pathological diagnosis of resection or biopsy, have a history of chemotherapy or radiation therapy, and have measurable lesions based on the RANO criteria. The patient's age of 65 meets the age requirement, and there is no mention of any exclusion criteria that would 

for i in range(len(df)):
    TargetCriteria = GetJRCTCriteria(df,i)
    AgentJudgment = CriteriaCheckAgent.evaluate_eligibility(TargetCriteria, ex_question)
    print(AgentJudgment)
    AgentGrade = grader_agent.evaluate_eligibility(AgentJudgment)
    print(AgentGrade)
    df.iloc[i,:]['AgentJudgment'] = AgentJudgment
    df.iloc[i,:]['AgentJudgment'] = AgentGrade


In [7]:
 # 列を指定した順に並び替え
columns_order = ['JRCT ID', 'Title', '研究・治験の目的','AgentJudgment', 'AgentGrade','主たる選択基準', '主たる除外基準','Inclusion Criteria','Exclusion Criteria','NCT No', 'JapicCTI No']
df = df[columns_order]